In [2]:
%pip install polars

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 805.7/805.7 kB 5.4 MB/s  0:00:00 eta 0:00:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 45.1/45.1 MB 37.2 MB/s  0:00:01m0:00:0100:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2/2 [polars]2m1/2 [polars]
Note: you may need to restart the kernel to use updated packages.


# Chapter 1

In [4]:
import polars as pl

In [8]:
! wc -l data/citibike/202403-citibike-tripdata_3.csv

663296 data/citibike/202403-citibike-tripdata_3.csv


In [9]:
! head -n 6 data/citibike/202403-citibike-tripdata_3.csv

ride_id,rideable_type,started_at,ended_at,start_station_name,start_station_id,end_station_name,end_station_id,start_lat,start_lng,end_lat,end_lng,member_casual
739F9ACBB2229887,electric_bike,2024-03-25 16:59:04.459,2024-03-25 17:05:32.885,18 St & 27 Ave,7062.07,21 Ave & Shore Blvd,7342.01,40.772768286288304,-73.92743647098541,40.783956,-73.916894,member
9B8B925918026FE8,classic_bike,2024-03-27 19:42:00.602,2024-03-27 20:14:56.040,W 74 St & Columbus Ave,7230.10,Columbus Ave & W 72 St,7175.05,40.7785669,-73.97754961,40.7770575,-73.97898475,member
B72C9122D6B99271,electric_bike,2024-03-22 10:01:51.759,2024-03-22 10:06:08.497,20 Ave & 42 St,7163.07,23 Ave & 31 St,7082.08,40.775415,-73.900063,40.77423301703027,-73.91274864321404,member
8C6881F9A10BD0A4,classic_bike,2024-03-19 17:27:15.692,2024-03-19 17:39:51.500,20 Ave & 42 St,7163.07,28 Ave & 44 St,6879.04,40.775415,-73.900063,40.76408932350688,-73.91065120697021,casual
CC5253575EF49E63,electric_bike,2024-03-24 09:38:16.550,2024-03-24 09:5

In [14]:
try:
    trips = pl.read_csv("data/citibike/202403-citibike-tripdata_3.csv",try_parse_dates=True)
except Exception as e:
    print(e)

could not parse `JC038` as dtype `f64` at column 'end_station_id' (column number 8)

The current offset in the file is 317626 bytes.

You might want to try:
- increasing `infer_schema_length` (e.g. `infer_schema_length=10000`),
- specifying correct dtype with the `schema_overrides` argument
- setting `ignore_errors` to `True`,
- adding `JC038` to the `null_values` list.

Original error: ```invalid primitive value found during CSV parsing```


polars read_csv with "end_station"

In [19]:
trips = pl.read_csv("data/citibike/202403-citibike-tripdata_3.csv",
try_parse_dates=True,
schema_overrides={
"start_station_id":pl.String,
"end_station_id":pl.String,
},
).sort("started_at")

trips.height, len(trips)

(663295, 663295)

In [20]:
%%time
trips.height

CPU times: user 10 μs, sys: 0 ns, total: 10 μs
Wall time: 13.6 μs


663295

In [22]:
%%time
len(trips)

CPU times: user 10 μs, sys: 2 μs, total: 12 μs
Wall time: 16 μs


663295

In [23]:
print(trips[:,:4])

shape: (663_295, 4)
┌──────────────────┬───────────────┬─────────────────────────┬─────────────────────────┐
│ ride_id          ┆ rideable_type ┆ started_at              ┆ ended_at                │
│ ---              ┆ ---           ┆ ---                     ┆ ---                     │
│ str              ┆ str           ┆ datetime[μs]            ┆ datetime[μs]            │
╞══════════════════╪═══════════════╪═════════════════════════╪═════════════════════════╡
│ 52974AA955B77FD3 ┆ electric_bike ┆ 2024-03-14 20:00:00.099 ┆ 2024-03-14 20:03:21.711 │
│ DE94DFC876960A4E ┆ classic_bike  ┆ 2024-03-14 20:00:00.931 ┆ 2024-03-14 20:10:43.662 │
│ C51F717D55C821F1 ┆ electric_bike ┆ 2024-03-14 20:00:03.850 ┆ 2024-03-14 20:10:32.170 │
│ FEEBE2FA2CA02D7E ┆ classic_bike  ┆ 2024-03-14 20:00:05.535 ┆ 2024-03-14 20:06:27.142 │
│ FC953940C57C2A35 ┆ electric_bike ┆ 2024-03-14 20:00:05.790 ┆ 2024-03-14 20:12:03.063 │
│ …                ┆ …             ┆ …                       ┆ …                       │
│

In [24]:
print(trips[:,4:8])

shape: (663_295, 4)
┌──────────────────────────┬──────────────────┬─────────────────────────────┬────────────────┐
│ start_station_name       ┆ start_station_id ┆ end_station_name            ┆ end_station_id │
│ ---                      ┆ ---              ┆ ---                         ┆ ---            │
│ str                      ┆ str              ┆ str                         ┆ str            │
╞══════════════════════════╪══════════════════╪═════════════════════════════╪════════════════╡
│ MacDougal St & Prince St ┆ 5687.04          ┆ Cleveland Pl & Spring St    ┆ 5492.05        │
│ 10 Ave & W 28 St         ┆ 6459.04          ┆ 8 Ave & W 16 St             ┆ 6072.11        │
│ Broadway & W 38 St       ┆ 6560.15          ┆ E 53 St & Lexington Ave     ┆ 6617.09        │
│ 8 Ave & W 16 St          ┆ 6072.11          ┆ W 26 St & 10 Ave            ┆ 6382.05        │
│ Greenwich St & Rector St ┆ 5073.07          ┆ Walker St & Baxter St       ┆ 5351.07        │
│ …                        ┆ …

In [25]:
print(trips[:,8:])

shape: (663_295, 5)
┌───────────┬────────────┬───────────┬────────────┬───────────────┐
│ start_lat ┆ start_lng  ┆ end_lat   ┆ end_lng    ┆ member_casual │
│ ---       ┆ ---        ┆ ---       ┆ ---        ┆ ---           │
│ f64       ┆ f64        ┆ f64       ┆ f64        ┆ str           │
╞═══════════╪════════════╪═══════════╪════════════╪═══════════════╡
│ 40.727103 ┆ -74.002971 ┆ 40.722104 ┆ -73.997249 ┆ member        │
│ 40.750664 ┆ -74.001768 ┆ 40.740983 ┆ -74.001702 ┆ member        │
│ 40.752973 ┆ -73.987349 ┆ 40.758281 ┆ -73.970694 ┆ casual        │
│ 40.740983 ┆ -74.001702 ┆ 40.749718 ┆ -74.00295  ┆ member        │
│ 40.708066 ┆ -74.01356  ┆ 40.717411 ┆ -73.999573 ┆ member        │
│ …         ┆ …          ┆ …         ┆ …          ┆ …             │
│ 40.67897  ┆ -73.978553 ┆ 40.679331 ┆ -73.975195 ┆ member        │
│ 40.725029 ┆ -73.990697 ┆ 40.723077 ┆ -73.985836 ┆ member        │
│ 40.761227 ┆ -73.96094  ┆ 40.759125 ┆ -73.962658 ┆ member        │
│ 40.729848 ┆ -73.974552 ┆ 4

In [27]:
! python -m json.tool data/citibike/nyc-neighborhoods.geojson

{
    "type": "FeatureCollection",
    "crs": {
        "type": "name",
        "properties": {
            "name": "urn:ogc:def:crs:OGC:1.3:CRS84"
        }
    },
    "features": [
        {
            "type": "Feature",
            "properties": {
                "neighborhood": "Allerton",
                "boroughCode": "2",
                "borough": "Bronx",
                "X.id": "http://nyc.pediacities.com/Resource/Neighborhood/Allerton"
            },
            "geometry": {
                "type": "Polygon",
                "coordinates": [
                    [
                        [
                            -73.84859700000018,
                            40.871670000000115
                        ],
                        [
                            -73.84582253683678,
                            40.870239076236174
                        ],
                        [
                            -73.85455918463374,
                            40.85995383576425
 

Let's Read the Json

In [32]:
nb = (pl.read_json("data/citibike/nyc-neighborhoods.geojson")
        .select("features").explode("features").unnest("features")
        .unnest("properties").select("neighborhood","borough","geometry")
         
        )

use (
    <br>.
    <br>.
    <br>.

) for better readilbity